In [1]:
from datasets import load_dataset, load_metric, Audio, Dataset
import os
import torchaudio
from tqdm.auto import tqdm

In [ ]:
%%bash 
wget https://www.openslr.org/resources/42/km_kh_male.zip
unzip km_kh_male.zip

--2022-02-03 05:13:35--  https://www.openslr.org/resources/42/km_kh_male.zip
Resolving www.openslr.org (www.openslr.org)... 46.101.158.64
Connecting to www.openslr.org (www.openslr.org)|46.101.158.64|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 866086951 (826M) [application/zip]
Saving to: ‘km_kh_male.zip’

     0K .......... .......... .......... .......... ..........  0%  264K 53m29s
    50K .......... .......... .......... .......... ..........  0%  525K 40m9s
   100K .......... .......... .......... .......... ..........  0%  523K 35m45s
   150K .......... .......... .......... .......... ..........  0%  523K 33m33s
   200K .......... .......... .......... .......... ..........  0%  264K 37m31s
   250K .......... .......... .......... .......... ..........  0%  523K 35m45s
   300K .......... .......... .......... .......... ..........  0%  526K 34m28s
   350K .......... .......... .......... .......... ..........  0%  524K 33m31s
   400K .......... ....

Archive:  km_kh_male.zip
   creating: km_kh_male/
  inflating: km_kh_male/line_index.tsv  
   creating: km_kh_male/wavs/
  inflating: km_kh_male/wavs/khm_1161_3945210975.wav  
  inflating: km_kh_male/wavs/khm_1161_3840820726.wav  
  inflating: km_kh_male/wavs/khm_1161_3632689663.wav  
  inflating: km_kh_male/wavs/khm_1161_3514535297.wav  
  inflating: km_kh_male/wavs/khm_1161_3445330166.wav  
  inflating: km_kh_male/wavs/khm_1161_3170598248.wav  
  inflating: km_kh_male/wavs/khm_1161_3030414325.wav  
  inflating: km_kh_male/wavs/khm_1161_2858870182.wav  
  inflating: km_kh_male/wavs/khm_1161_2835582962.wav  
  inflating: km_kh_male/wavs/khm_1161_2662937440.wav  
  inflating: km_kh_male/wavs/khm_1161_2449542221.wav  
  inflating: km_kh_male/wavs/khm_1161_2294049689.wav  
  inflating: km_kh_male/wavs/khm_1161_2136371765.wav  
  inflating: km_kh_male/wavs/khm_1161_2092267195.wav  
  inflating: km_kh_male/wavs/khm_1161_2061040949.wav  
  inflating: km_kh_male/wavs/khm_1161_2054764716.wav  

### Load KH Data

In [4]:
from sklearn.model_selection import train_test_split
import pandas as pd
from datasets import load_dataset
 
colnames=['path','drop','text'] 
df  = pd.read_csv('km_kh_male/line_index.tsv',sep='\t',header=None,names=colnames)
df['path'] = '/workspace/xls-r-300m-km/km_kh_male/wavs/'+df['path'] +'.wav'

train, test = train_test_split(df, test_size=0.1)

train.to_csv('./km_kh_male/line_index_train.csv')
test.to_csv('./km_kh_male/line_index_test.csv')

In [5]:
common_voice_train = load_dataset('csv', data_files='km_kh_male/line_index_train.csv', split= 'train')
common_voice_test  = load_dataset('csv', data_files='km_kh_male/line_index_test.csv', split = 'train')

Using custom data configuration default-9437ac7a59e13b5b


  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

Dataset csv downloaded and prepared to /workspace/.cache/huggingface/datasets/csv/default-9437ac7a59e13b5b/0.0.0/6b9057d9e23d9d8a2f05b985917a0da84d70c5dae3d22ddd8a3f22fb01c69d9e. Subsequent calls will reuse this data.


Using custom data configuration default-fbad308ab5a03eb2


  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

Dataset csv downloaded and prepared to /workspace/.cache/huggingface/datasets/csv/default-fbad308ab5a03eb2/0.0.0/6b9057d9e23d9d8a2f05b985917a0da84d70c5dae3d22ddd8a3f22fb01c69d9e. Subsequent calls will reuse this data.


In [6]:
common_voice_train = (common_voice_train
                      .remove_columns(["Unnamed: 0", "drop"])
                      .rename_column('text', 'sentence'))
common_voice_test  = (common_voice_test
                      .remove_columns(["Unnamed: 0", "drop"])
                      .rename_column('text', 'sentence'))

### Clean Up the Text

In [6]:
# Remove character
import re
chars_to_remove_regex = '[\,\?\.\!\-\;\:\"\“\%\‘\”\�\']'

def remove_special_characters(batch):
    batch["sentence"] = re.sub(chars_to_remove_regex, '', batch["sentence"])
    return batch

In [7]:
# TODO: somehow this break thigns. WHY?
common_voice_train = common_voice_train.map(remove_special_characters, num_proc=16)
common_voice_test = common_voice_test.map(remove_special_characters, num_proc=16)

Loading cached processed dataset at /workspace/.cache/huggingface/datasets/common_voice/tr/6.1.0/5693bfc0feeade582a78c2fb250bc88f52bd86f0a7f1bb22bfee67e715de30fd/cache-00e6eaf49d7a0a72.arrow
Loading cached processed dataset at /workspace/.cache/huggingface/datasets/common_voice/tr/6.1.0/5693bfc0feeade582a78c2fb250bc88f52bd86f0a7f1bb22bfee67e715de30fd/cache-a5c6e0729d04ce41.arrow
Loading cached processed dataset at /workspace/.cache/huggingface/datasets/common_voice/tr/6.1.0/5693bfc0feeade582a78c2fb250bc88f52bd86f0a7f1bb22bfee67e715de30fd/cache-ce6c54a59fe05e35.arrow
Loading cached processed dataset at /workspace/.cache/huggingface/datasets/common_voice/tr/6.1.0/5693bfc0feeade582a78c2fb250bc88f52bd86f0a7f1bb22bfee67e715de30fd/cache-29d8049f5c2dba0e.arrow
Loading cached processed dataset at /workspace/.cache/huggingface/datasets/common_voice/tr/6.1.0/5693bfc0feeade582a78c2fb250bc88f52bd86f0a7f1bb22bfee67e715de30fd/cache-1df366b8d10cfb25.arrow
Loading cached processed dataset at /workspac

In [7]:
common_voice_train[0]

{'path': '/workspace/xls-r-300m-km/km_kh_male/wavs/khm_6753_2783635929.wav',
 'sentence': 'កុងដ្វាណា មាន មូលដ្ឋាន នៅ ប្រទេស ស៊ីរី'}

### Build Character

In [8]:
vocab_train = []
vocab_test  = []

for batch in tqdm(common_voice_train):
    sentence = batch['sentence']
    vocab_train.extend(list(set(list(sentence))))
    
for batch in tqdm(common_voice_test):
    sentence = batch['sentence']
    vocab_test.extend(list(set(list(sentence))))

  0%|          | 0/2615 [00:00<?, ?it/s]

  0%|          | 0/291 [00:00<?, ?it/s]

In [9]:
vocab_list = list(set(vocab_train) | set(vocab_test))
vocab_dict = {v: k for k, v in enumerate(sorted(vocab_list))}

In [10]:
print(vocab_dict)

{' ': 0, 'ក': 1, 'ខ': 2, 'គ': 3, 'ឃ': 4, 'ង': 5, 'ច': 6, 'ឆ': 7, 'ជ': 8, 'ឈ': 9, 'ញ': 10, 'ដ': 11, 'ឋ': 12, 'ឌ': 13, 'ឍ': 14, 'ណ': 15, 'ត': 16, 'ថ': 17, 'ទ': 18, 'ធ': 19, 'ន': 20, 'ប': 21, 'ផ': 22, 'ព': 23, 'ភ': 24, 'ម': 25, 'យ': 26, 'រ': 27, 'ល': 28, 'វ': 29, 'ស': 30, 'ហ': 31, 'ឡ': 32, 'អ': 33, 'ឥ': 34, 'ឧ': 35, 'ឪ': 36, 'ឫ': 37, 'ឬ': 38, 'ឭ': 39, 'ឮ': 40, 'ឯ': 41, 'ឱ': 42, 'ា': 43, 'ិ': 44, 'ី': 45, 'ឹ': 46, 'ឺ': 47, 'ុ': 48, 'ូ': 49, 'ួ': 50, 'ើ': 51, 'ឿ': 52, 'ៀ': 53, 'េ': 54, 'ែ': 55, 'ៃ': 56, 'ោ': 57, 'ៅ': 58, 'ំ': 59, 'ះ': 60, 'ៈ': 61, '៉': 62, '៊': 63, '់': 64, '៌': 65, '៍': 66, '៎': 67, '៏': 68, '័': 69, '្': 70}


In [11]:
# make the space more intuitive to understand
vocab_dict["|"] = vocab_dict[" "]
del vocab_dict[" "]

vocab_dict["[UNK]"] = len(vocab_dict)
vocab_dict["[PAD]"] = len(vocab_dict)
len(vocab_dict)

73

In [12]:
print(vocab_dict)

{'ក': 1, 'ខ': 2, 'គ': 3, 'ឃ': 4, 'ង': 5, 'ច': 6, 'ឆ': 7, 'ជ': 8, 'ឈ': 9, 'ញ': 10, 'ដ': 11, 'ឋ': 12, 'ឌ': 13, 'ឍ': 14, 'ណ': 15, 'ត': 16, 'ថ': 17, 'ទ': 18, 'ធ': 19, 'ន': 20, 'ប': 21, 'ផ': 22, 'ព': 23, 'ភ': 24, 'ម': 25, 'យ': 26, 'រ': 27, 'ល': 28, 'វ': 29, 'ស': 30, 'ហ': 31, 'ឡ': 32, 'អ': 33, 'ឥ': 34, 'ឧ': 35, 'ឪ': 36, 'ឫ': 37, 'ឬ': 38, 'ឭ': 39, 'ឮ': 40, 'ឯ': 41, 'ឱ': 42, 'ា': 43, 'ិ': 44, 'ី': 45, 'ឹ': 46, 'ឺ': 47, 'ុ': 48, 'ូ': 49, 'ួ': 50, 'ើ': 51, 'ឿ': 52, 'ៀ': 53, 'េ': 54, 'ែ': 55, 'ៃ': 56, 'ោ': 57, 'ៅ': 58, 'ំ': 59, 'ះ': 60, 'ៈ': 61, '៉': 62, '៊': 63, '់': 64, '៌': 65, '៍': 66, '៎': 67, '៏': 68, '័': 69, '្': 70, '|': 0, '[UNK]': 71, '[PAD]': 72}


In [13]:
import json
with open('vocab.json', 'w') as vocab_file:
    json.dump(vocab_dict, vocab_file)

# Tokenizer

In [14]:
from transformers import Wav2Vec2CTCTokenizer
from transformers import Wav2Vec2FeatureExtractor
from transformers import Wav2Vec2Processor

In [15]:
tokenizer = Wav2Vec2CTCTokenizer.from_pretrained("./", unk_token="[UNK]", pad_token="[PAD]", word_delimiter_token="|")  # './' load vocab.json in the current directory
feature_extractor = Wav2Vec2FeatureExtractor(feature_size=1, sampling_rate=16000, padding_value=0.0, do_normalize=True, return_attention_mask=True)  
processor = Wav2Vec2Processor(feature_extractor=feature_extractor, tokenizer=tokenizer)

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [26]:
# def speech_file_to_array_fn(batch):
#     audio_array, sampling_rate = torchaudio.load(batch["path"])
#     batch["audio"] = {
#         "array": audio_array[0].numpy(),
#         "path": batch["path"],
#         "sampling_rate": sampling_rate
#     }
#     return batch

In [27]:
# common_voice_train = common_voice_train.map(speech_file_to_array_fn)
# common_voice_test = common_voice_test.map(speech_file_to_array_fn)

0ex [00:00, ?ex/s]

0ex [00:00, ?ex/s]

In [17]:
common_voice_train = common_voice_train.cast_column("path", Audio(sampling_rate=16_000)).rename_column('path', 'audio')
common_voice_test  = common_voice_test.cast_column("path", Audio(sampling_rate=16_000)).rename_column('path', 'audio')

In [18]:
common_voice_train[0]

{'audio': {'path': '/workspace/xls-r-300m-km/km_kh_male/wavs/khm_6753_2783635929.wav',
  'array': array([ 3.3284457e-05,  5.5497538e-05,  2.6061889e-05, ...,
          2.0593125e-06, -5.3043197e-05,  0.0000000e+00], dtype=float32),
  'sampling_rate': 16000},
 'sentence': 'កុងដ្វាណា មាន មូលដ្ឋាន នៅ ប្រទេស ស៊ីរី'}

In [19]:
import IPython.display as ipd
import numpy as np
import random

rand_int = random.randint(0, len(common_voice_train)-1)

print("Target text:", common_voice_train[rand_int]["sentence"])
print("Input array shape:", common_voice_train[rand_int]["audio"]["array"].shape)
print("Sampling rate:", common_voice_train[rand_int]["audio"]["sampling_rate"])
ipd.Audio(data=common_voice_train[rand_int]["audio"]["array"], autoplay=True, rate=16000)

Target text: ផ្សារ អូឡាំពិក មាន ក្រណាត់ និង សម្លៀកបំពាក់ បោះ ដុំ និង លក់ រាយ
Input array shape: (81920,)
Sampling rate: 16000


In [20]:
# This does not prepare the input for the Transformer model.
# This will resample the data and convert the sentence into indices
# Batch here is just for one entry (row)
def prepare_dataset(batch):
    audio = batch["audio"]
    
    # batched output is "un-batched"
    batch["input_values"] = processor(audio["array"], sampling_rate=audio["sampling_rate"]).input_values[0]
    batch["input_length"] = len(batch["input_values"])
    
    with processor.as_target_processor():
        batch["labels"] = processor(batch["sentence"]).input_ids
    return batch

In [22]:
common_voice_train = common_voice_train.map(prepare_dataset, remove_columns=common_voice_train.column_names, num_proc=16)
common_voice_test = common_voice_test.map(prepare_dataset, remove_columns=common_voice_test.column_names, num_proc=16)

In [41]:
# In case the dataset is too long which can lead to OOM. We should filter them out.
# max_input_length_in_sec = 5.0
# common_voice_train = common_voice_train.filter(lambda x: x < max_input_length_in_sec * processor.feature_extractor.sampling_rate, input_columns=["input_length"])

In [25]:
import torch

from dataclasses import dataclass, field
from typing import Any, Dict, List, Optional, Union

@dataclass
class DataCollatorCTCWithPadding:
    """
    Data collator that will dynamically pad the inputs received.
    Args:
        processor (:class:`~transformers.Wav2Vec2Processor`)
            The processor used for proccessing the data.
        padding (:obj:`bool`, :obj:`str` or :class:`~transformers.tokenization_utils_base.PaddingStrategy`, `optional`, defaults to :obj:`True`):
            Select a strategy to pad the returned sequences (according to the model's padding side and padding index)
            among:
            * :obj:`True` or :obj:`'longest'`: Pad to the longest sequence in the batch (or no padding if only a single
              sequence if provided).
            * :obj:`'max_length'`: Pad to a maximum length specified with the argument :obj:`max_length` or to the
              maximum acceptable input length for the model if that argument is not provided.
            * :obj:`False` or :obj:`'do_not_pad'` (default): No padding (i.e., can output a batch with sequences of
              different lengths).
    """

    processor: Wav2Vec2Processor
    padding: Union[bool, str] = True

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lenghts and need
        # different padding methods
        input_features = [{"input_values": feature["input_values"]} for feature in features]
        label_features = [{"input_ids": feature["labels"]} for feature in features]

        batch = self.processor.pad(
            input_features,
            padding=self.padding,
            return_tensors="pt",
        )

        with self.processor.as_target_processor():
            labels_batch = self.processor.pad(
                label_features,
                padding=self.padding,
                return_tensors="pt",
            )

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        batch["labels"] = labels

        return batch

In [26]:
data_collator = DataCollatorCTCWithPadding(processor=processor, padding=True)

In [27]:
wer_metric = load_metric("wer")
# cer_metric = load_metric("cer")

In [44]:
def compute_metrics(pred):
    pred_logits = pred.predictions
    pred_ids = np.argmax(pred_logits, axis=-1)

    pred.label_ids[pred.label_ids == -100] = tokenizer.pad_token_id

    pred_str = tokenizer.batch_decode(pred_ids)
    label_str = tokenizer.batch_decode(pred.label_ids, group_tokens=False)

    print("pred : ", pred_ids[0])
    print("label: ", pred.label_ids[0])
    print("-----------------")
    
    wer = wer_metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}

In [45]:
from transformers import Wav2Vec2ForCTC

model = Wav2Vec2ForCTC.from_pretrained(
    "facebook/wav2vec2-xls-r-300m", 
    attention_dropout=0.1,
    layerdrop=0.0,
    feat_proj_dropout=0.0,
    mask_time_prob=0.75, 
    mask_time_length=10,
    mask_feature_prob=0.25,
    mask_feature_length=64,
    ctc_loss_reduction="mean",
    pad_token_id=processor.tokenizer.pad_token_id,
    vocab_size=len(processor.tokenizer)
)

loading configuration file https://huggingface.co/facebook/wav2vec2-xls-r-300m/resolve/main/config.json from cache at /workspace/.cache/huggingface/transformers/dabc27df63e37bd2a7a221c7774e35f36a280fbdf917cf54cadfc7df8c786f6f.a3e4c3c967d9985881e0ae550a5f6f668f897db5ab2e0802f9b97973b15970e6
Model config Wav2Vec2Config {
  "activation_dropout": 0.0,
  "adapter_kernel_size": 3,
  "adapter_stride": 2,
  "add_adapter": false,
  "apply_spec_augment": true,
  "architectures": [
    "Wav2Vec2ForPreTraining"
  ],
  "attention_dropout": 0.1,
  "bos_token_id": 1,
  "classifier_proj_size": 256,
  "codevector_dim": 768,
  "contrastive_logits_temperature": 0.1,
  "conv_bias": true,
  "conv_dim": [
    512,
    512,
    512,
    512,
    512,
    512,
    512
  ],
  "conv_kernel": [
    10,
    3,
    3,
    3,
    3,
    2,
    2
  ],
  "conv_stride": [
    5,
    2,
    2,
    2,
    2,
    2,
    2
  ],
  "ctc_loss_reduction": "mean",
  "ctc_zero_infinity": false,
  "diversity_loss_weight": 0.1,
 

In [46]:
model.freeze_feature_encoder()

In [47]:
from transformers import TrainingArguments

training_args = TrainingArguments(
  output_dir='.',
  group_by_length=True,
  per_device_train_batch_size=8,
  gradient_accumulation_steps=4,
  evaluation_strategy="steps",
  gradient_checkpointing=True,
  fp16=True,
  num_train_epochs=50,
  save_steps=400,
  eval_steps=400,
  logging_steps=100,
  learning_rate=5e-5,
  warmup_steps=1000,
  save_total_limit=3,
  load_best_model_at_end=True
)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).


In [48]:
from transformers import Trainer

trainer = Trainer(
    model=model,
    data_collator=data_collator,
    args=training_args,
    compute_metrics=compute_metrics,
    train_dataset=common_voice_train,
    eval_dataset=common_voice_test,
    tokenizer=processor.feature_extractor,
)

Using amp half precision backend


In [49]:
trainer.train()

The following columns in the training set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
/opt/conda/lib/python3.8/site-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use thePyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 2615
  Num Epochs = 50
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 32
  Gradient Accumulation steps = 4
  Total optimization steps = 4050


The following columns in the evaluation set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
***** Running Evaluation *****
  Num examples = 291
  Batch size = 8


pred :  [72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 

Saving model checkpoint to ./checkpoint-400
Configuration saved in ./checkpoint-400/config.json
Model weights saved in ./checkpoint-400/pytorch_model.bin
Configuration saved in ./checkpoint-400/preprocessor_config.json
The following columns in the evaluation set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
***** Running Evaluation *****
  Num examples = 291
  Batch size = 8


pred :  [72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 

...

pred :  [30 63 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 11 44 72 72 72 72  6 72  0 72 25 62 49 49 72
 72 72 72 16 49 72 72 72 72 72  0 72 20 58 72 72  0  0 72 72 23 54 72 72
 72 28  0 72 11 55 72 72 28  0  0 72 72 21 70 70 27 51 72 72 72 72 72 72
  0  0  0 42 70 72 72 72 26  0  0 72 11 48 72 72 72 21 64 64  0 72 72 30
 72 72 72 72 72 25 72 72 72 72 23 54 72 72 72 27 27 72 72 72 72 72 72 72
  0  0 72 72 72 72 72 72  3 70 72 27 52 72 72 72  5  0  0 72 30 30 44 72
 72  5 70 70 72 31 43 72 72 72 72 72 72 72 72 72 27 44 72 72 72 72 25 72
 72  0  0 72 72 26 72 72 72 72 72  1 72  0 72 18 58 72 72  0  0  0 33 70
 72 72 72 72 72 72 26 72  0  0 72 72 72 25 50 72 72 72 72 72 72 72 26 26
  0  0 72 20 58 72 72 72 72 72  0 72 25 72 72 70 70 72 11 48 72 72 72 72
 72 59 72 72  0 72 72 29 16 72 72 72 72 70 16 72  0  0 72 30 72 72 72 25
 70 72 72 27 72 72 72 72  5 72  0 33 72 72 15 70 70 72 11 55 72 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 

Saving model checkpoint to ./checkpoint-3600
Configuration saved in ./checkpoint-3600/config.json
Model weights saved in ./checkpoint-3600/pytorch_model.bin
Configuration saved in ./checkpoint-3600/preprocessor_config.json
Deleting older checkpoint [checkpoint-2400] due to args.save_total_limit
The following columns in the evaluation set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
***** Running Evaluation *****
  Num examples = 291
  Batch size = 8


pred :  [30 63 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72 72
 72 72 72 72 72 72 72 72 72 11 43 72 72 72 72  6 72  0 72 25 62 62 49 72
 72 72 72 16 49 72 72 72 72 72  0 72 20 58 72 72  0  0 72 72 23 54 18 72
 72 28  0  0 11 55 72 72 28  0  0 72 72 21 70 70 27 51 72 72 72 72 72 72
  0  0  0 42 70 72 72 72 26  0  0 72 11 48 72 72 72 21 21 64  0 72 72 30
 30 72 72 72 72 25 72 72 72 72 23 54 72 72 72 27 27 72 72 72 72 72 72 72
  0  0 72 72 72 72 72 72  3 70 72 27 52 72 72 72  5  0  0 72 30 30 44 72
 72  5 70 70 72 31 43 72 72 72 72 72 72 72 72 72 27 46 72 72 72 72 25 72
 72  0  0 72 72 26 72 72 72 72 72  1 72  0 72 18 58 72 72  0  0  0 33 70
 72 72 72 72 72 72 26 72  0  0 72 72 72 25 50 72 72 72 72 72 72 72 26 26
  0  0 72 20 58 72 72 72 72 72  0 72 25 72 70 70 70 72 11 48 72 72 72 72
 72 59 72 72  0 72 72 29 16 72 72 72 70 70 16 72  0  0 72 30 72 72 72 25
 72 72 72 27 72 72 72 72  5 72  0 33 72 72 15 70 70 72 72 12 55 72 72 72
 72 72 72 72 72 72 72 72 72 72 72 72 72 72 

Saving model checkpoint to ./checkpoint-4000
Configuration saved in ./checkpoint-4000/config.json
Model weights saved in ./checkpoint-4000/pytorch_model.bin
Configuration saved in ./checkpoint-4000/preprocessor_config.json
Deleting older checkpoint [checkpoint-2800] due to args.save_total_limit


Training completed. Do not forget to share your model on huggingface.co/models =)


Loading best model from ./checkpoint-4000 (score: 0.46376487612724304).


TrainOutput(global_step=4050, training_loss=2.89372775796019, metrics={'train_runtime': 8168.6927, 'train_samples_per_second': 16.006, 'train_steps_per_second': 0.496, 'total_flos': 1.9735608328149316e+19, 'train_loss': 2.89372775796019, 'epoch': 49.99})

In [57]:
tokenizer.push_to_hub('vitouphy/xls-r-300m-km')

tokenizer config file saved in vitouphy/xls-r-300m-km/tokenizer_config.json
Special tokens file saved in vitouphy/xls-r-300m-km/special_tokens_map.json
added tokens file saved in vitouphy/xls-r-300m-km/added_tokens.json


In [53]:
kwargs = {
    "finetuned_from": "facebook/wav2vec2-xls-r-300m",
    "tasks": "speech-recognition",
    "tags": ["automatic-speech-recognition", "openslr", "robust-speech-event", "km"],
    "dataset_args": f"Config: km, Training split: train+validation, Eval split: test",
    "dataset": "openslr",
    "language": "km"
}

In [54]:
trainer.create_model_card(**kwargs)

Dropping the following result as it does not have all the necessary fields:
{}


In [58]:
model.push_to_hub('vitouphy/xls-r-300m-km')

Configuration saved in vitouphy/xls-r-300m-km/config.json
Model weights saved in vitouphy/xls-r-300m-km/pytorch_model.bin
Several commits (2) will be pushed upstream.
The progress bars may be unreliable.


Upload file pytorch_model.bin:   0%|          | 3.39k/1.18G [00:00<?, ?B/s]

To https://huggingface.co/vitouphy/xls-r-300m-km
   e25c362..dff1f30  main -> main



'https://huggingface.co/vitouphy/xls-r-300m-km/commit/dff1f3008b5c2afbbbcab722e17fded4bf8f782b'

In [59]:
trainer.save_model()

Saving model checkpoint to .
Configuration saved in ./config.json
Model weights saved in ./pytorch_model.bin
Configuration saved in ./preprocessor_config.json
